In [316]:

import time
import requests
from bs4 import BeautifulSoup
import pymongo
import pandas as pd
import numpy as np
import re

from sklearn.externals import joblib

from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
wnlzer = WordNetLemmatizer()


from pprint import pprint
from time import time
import logging


from collections import defaultdict
from gensim import corpora, models
from gensim.similarities import MatrixSimilarity

import sys
import os
import csv
import shutil
from collections import defaultdict

from sklearn.linear_model import SGDClassifier, Perceptron
from sklearn.feature_extraction.text import TfidfVectorizer, TfidfTransformer, CountVectorizer
from sklearn.naive_bayes import MultinomialNB
from sklearn.svm import LinearSVC
from sklearn.model_selection import GridSearchCV, ParameterGrid
from sklearn.pipeline import Pipeline
from sklearn.datasets import load_files
from sklearn.model_selection import train_test_split
from sklearn import metrics
from sklearn.metrics import roc_auc_score
#import parfit.parfit as pf

import matplotlib.pyplot as plt

source_path = 'test_data'
#source_file = 'test_strains_reviews.csv'
target_path = '/Users/jordanweil/green_rex/test_data'

In [144]:
test_reviews = pd.read_csv("./../../new_full_test_strains_reviews.csv")

In [242]:
new_tr = test_reviews.drop([3570,2728,355], axis=0)

In [337]:
new_tr.columns

Index(['Unnamed: 0', 'hybrid/blue-dream', 'sativa/sour-diesel', 'hybrid/gsc',
       'sativa/green-crack', 'hybrid/og-kush', 'indica/granddaddy-purple',
       'hybrid/original-glue', 'hybrid/white-widow', 'hybrid/blue-dream.1',
       'sativa/sour-diesel.1', 'hybrid/gsc.1', 'sativa/green-crack.1',
       'hybrid/og-kush.1', 'indica/granddaddy-purple.1',
       'hybrid/original-glue.1', 'hybrid/white-widow.1', 'sativa/jack-herer',
       'indica/bubba-kush', 'hybrid/pineapple-express', 'hybrid/trainwreck',
       'hybrid/ak-47', 'sativa/durban-poison', 'indica/northern-lights',
       'hybrid/headband', 'indica/blue-cheese', 'sativa/strawberry-cough',
       'hybrid/chemdawg', 'indica/purple-kush', 'sativa/lemon-haze',
       'sativa/super-lemon-haze', 'indica/grape-ape', 'indica/blueberry',
       'sativa/alaskan-thunder-fuck', 'sativa/super-silver-haze',
       'indica/blackberry-kush', 'hybrid/cherry-pie', 'indica/master-kush',
       'hybrid/skywalker-og', 'hybrid/cheese', 'indica/

In [248]:
mask = np.column_stack([new_tr[col].str.contains(r"ke thick robust problem going coughing thats alway", na=False) for col in new_tr])
new_tr.loc[mask.any(axis=1)]

Empty DataFrame
Columns: [Unnamed: 0, hybrid/blue-dream, sativa/sour-diesel, hybrid/gsc, sativa/green-crack, hybrid/og-kush, indica/granddaddy-purple, hybrid/original-glue, hybrid/white-widow, hybrid/blue-dream.1, sativa/sour-diesel.1, hybrid/gsc.1, sativa/green-crack.1, hybrid/og-kush.1, indica/granddaddy-purple.1, hybrid/original-glue.1, hybrid/white-widow.1, sativa/jack-herer, indica/bubba-kush, hybrid/pineapple-express, hybrid/trainwreck, hybrid/ak-47, sativa/durban-poison, indica/northern-lights, hybrid/headband, indica/blue-cheese, sativa/strawberry-cough, hybrid/chemdawg, indica/purple-kush, sativa/lemon-haze, sativa/super-lemon-haze, indica/grape-ape, indica/blueberry, sativa/alaskan-thunder-fuck, sativa/super-silver-haze, indica/blackberry-kush, hybrid/cherry-pie, indica/master-kush, hybrid/skywalker-og, hybrid/cheese, indica/death-star, sativa/chocolope, sativa/amnesia-haze, hybrid/tahoe-og, sativa/maui-wowie, hybrid/platinum-gsc, sativa/harlequin, indica/gods-gift, indica/la-confidential, hybrid/agent-orange, indica/purple-urkle, hybrid/lemon-kush, hybrid/mazar-x-blueberry, hybrid/golden-goat, indica/afghan-kush, hybrid/dutch-treat, indica/hindu-kush]
Index: []

[0 rows x 57 columns]

In [252]:
to_drop = ['Unnamed: 0','hybrid/blue-dream.1',
       'sativa/sour-diesel.1', 'hybrid/gsc.1', 'sativa/green-crack.1',
       'hybrid/og-kush.1', 'indica/granddaddy-purple.1',
       'hybrid/original-glue.1', 'hybrid/white-widow.1','hybrid/skywalker-og']

In [338]:
tr = new_tr.drop(to_drop, axis=1)
#blue_dream = tr['hybrid/blue-dream'].dropna().tolist() 
tr

hybrid/blue-dream  \
0                                                   NaN   
1                                                   NaN   
2                                                   NaN   
3                                                   NaN   
4     purchased sqdc quebec blue dream aurora thc bo...   
5                                                   NaN   
6                                                   NaN   
7     ehlers danlos syndrome constantly battling chr...   
8                                                   NaN   
9     tried first time today took two small hit vape...   
10                                                  NaN   
11                                                  NaN   
12                                                  NaN   
13                                                  NaN   
14                                                  NaN   
15                                                  NaN   
16                                                  NaN   
17                                                  NaN   
18                                                  NaN   
19                                                  NaN   
20    dream right try smoking bed youll good night r...   
21    got relaxed put chair set haze watching tvenjoyed   
22                                                  NaN   
23    review vape im smoking actually cartridge abxi...   
24                                                  NaN   
25                                                  NaN   
26                                                  NaN   
27                                                  NaN   
28                                                  NaN   
29                                                  NaN   
...                                                 ...   
5265                   hand dopest dope ive ever smoked   
5266                                                NaN   
5267                                                NaN   
5268                                                NaN   
5269                                                NaN   
5270                                                NaN   
5271                            always great smoke sesh   
5272                                                NaN   
5273                                                NaN   
5274                                                NaN   
5275                                                NaN   
5276                                                NaN   
5277                                                NaN   
5278                                                NaN   
5279                                                NaN   
5280                                                NaN   
5281                                                NaN   
5282                                                NaN   
5283                                                NaN   
5284  im new smoker trying blue dream made feel drun...   
5285                                                NaN   
5286                                                NaN   
5287                                                NaN   
5288                                                NaN   
5289                                                NaN   
5290                                                NaN   
5291                                                NaN   
5292                                                NaN   
5293                                                NaN   
5294                                                NaN   

                                     sativa/sour-diesel  \
0                                                   NaN   
1                                                   NaN   
2                                                   NaN   
3                                                   NaN   
4                                                   NaN   
5     best looking bud op

In [294]:
def cols_2_string(df):
    strain_list = []
    cols = df.columns
    for i in cols:
        strain = df[i].dropna().tolist()
        strain_str = " ".join(strain)
        strain_list.append(strain_str)
    return strain_list

In [339]:
col_string = cols_2_string(tr)
#tr['hybrid/blue-dream']
col_string

'purchased sqdc quebec blue dream aurora thc bought thought would strong sensitive thc loaded utilian g blue dream manit great felt mild head high came almost immediatly felt calm happy slightly uplifted energetic like pure sativa minute felt even relaxed throughout ehlers danlos syndrome constantly battling chronic pain blue dream one best come across relieve pain day time use also fight number stemming ailment ed tried first time today took two small hit vape waited minute thought hadnt vaped enough kicked high relaxing still get good head buzz well great chilling couch also productive want took almost pain away kicked happy blue dream dream right try smoking bed youll good night rest classic og kush blue dream forever brighten blue mood moon got relaxed put chair set haze watching tvenjoyed review vape im smoking actually cartridge abxi really looking forward trying fact maybe done thing read rave review couldnt wait get well tell feel pretty darn good right ive taken one hit minute

In [300]:
# Lowercase each document, split it by white space and filter out stopwords
texts = [[word for word in document.split()]for document in col_string]

[['purchased',
  'sqdc',
  'quebec',
  'blue',
  'dream',
  'aurora',
  'thc',
  'bought',
  'thought',
  'would',
  'strong',
  'sensitive',
  'thc',
  'loaded',
  'utilian',
  'g',
  'blue',
  'dream',
  'manit',
  'great',
  'felt',
  'mild',
  'head',
  'high',
  'came',
  'almost',
  'immediatly',
  'felt',
  'calm',
  'happy',
  'slightly',
  'uplifted',
  'energetic',
  'like',
  'pure',
  'sativa',
  'minute',
  'felt',
  'even',
  'relaxed',
  'throughout',
  'ehlers',
  'danlos',
  'syndrome',
  'constantly',
  'battling',
  'chronic',
  'pain',
  'blue',
  'dream',
  'one',
  'best',
  'come',
  'across',
  'relieve',
  'pain',
  'day',
  'time',
  'use',
  'also',
  'fight',
  'number',
  'stemming',
  'ailment',
  'ed',
  'tried',
  'first',
  'time',
  'today',
  'took',
  'two',
  'small',
  'hit',
  'vape',
  'waited',
  'minute',
  'thought',
  'hadnt',
  'vaped',
  'enough',
  'kicked',
  'high',
  'relaxing',
  'still',
  'get',
  'good',
  'head',
  'buzz',
  'well'

In [301]:
#Count word frequencies
from collections import defaultdict
frequency = defaultdict(int)
for text in texts:
    for token in text:
        frequency[token] += 1

In [340]:
frequency

defaultdict(int,
            {'purchased': 50,
             'sqdc': 4,
             'quebec': 3,
             'blue': 235,
             'dream': 193,
             'aurora': 3,
             'thc': 229,
             'bought': 99,
             'thought': 221,
             'would': 547,
             'strong': 468,
             'sensitive': 18,
             'loaded': 14,
             'utilian': 1,
             'g': 51,
             'manit': 1,
             'great': 1703,
             'felt': 411,
             'mild': 80,
             'head': 546,
             'high': 2474,
             'came': 83,
             'almost': 296,
             'immediatly': 2,
             'calm': 187,
             'happy': 570,
             'slightly': 76,
             'uplifted': 97,
             'energetic': 253,
             'like': 1768,
             'pure': 79,
             'sativa': 698,
             'minute': 240,
             'even': 359,
             'relaxed': 459,
             'throughout': 59,
      

In [341]:
# Only keep words that appear more than once
processed_corpus = [[token for token in text if frequency[token] > 1] for text in texts]

In [342]:
print(processed_corpus)

[['purchased', 'sqdc', 'quebec', 'blue', 'dream', 'aurora', 'thc', 'bought', 'thought', 'would', 'strong', 'sensitive', 'thc', 'loaded', 'g', 'blue', 'dream', 'great', 'felt', 'mild', 'head', 'high', 'came', 'almost', 'immediatly', 'felt', 'calm', 'happy', 'slightly', 'uplifted', 'energetic', 'like', 'pure', 'sativa', 'minute', 'felt', 'even', 'relaxed', 'throughout', 'syndrome', 'constantly', 'battling', 'chronic', 'pain', 'blue', 'dream', 'one', 'best', 'come', 'across', 'relieve', 'pain', 'day', 'time', 'use', 'also', 'fight', 'number', 'ailment', 'ed', 'tried', 'first', 'time', 'today', 'took', 'two', 'small', 'hit', 'vape', 'waited', 'minute', 'thought', 'hadnt', 'vaped', 'enough', 'kicked', 'high', 'relaxing', 'still', 'get', 'good', 'head', 'buzz', 'well', 'great', 'chilling', 'couch', 'also', 'productive', 'want', 'took', 'almost', 'pain', 'away', 'kicked', 'happy', 'blue', 'dream', 'dream', 'right', 'try', 'smoking', 'bed', 'youll', 'good', 'night', 'rest', 'classic', 'og', 'k

In [305]:
dictionary = corpora.Dictionary(processed_corpus)
pprint(dictionary)
dictionary.save('new_strains.dict')  # store the dictionary, for future reference

2019-04-10 16:04:54,137 : INFO : adding document #0 to Dictionary(0 unique tokens: [])
2019-04-10 16:04:54,290 : INFO : built Dictionary(5822 unique tokens: ['ab', 'able', 'absolute', 'absolutely', 'abundance']...) from 47 documents (total 149613 corpus positions)
2019-04-10 16:04:54,291 : INFO : saving Dictionary object under new_strains.dict, separately None
2019-04-10 16:04:54,293 : WARNING : this function is deprecated, use smart_open.open instead
2019-04-10 16:04:54,298 : INFO : saved new_strains.dict


In [343]:
print(dictionary.token2id)

{'ab': 0, 'able': 1, 'absolute': 2, 'absolutely': 3, 'abundance': 4, 'accompanied': 5, 'accomplish': 6, 'accurate': 7, 'ache': 8, 'acheter': 9, 'achieve': 10, 'across': 11, 'acting': 12, 'active': 13, 'activity': 14, 'actual': 15, 'actually': 16, 'acute': 17, 'add': 18, 'adderall': 19, 'adhd': 20, 'adjust': 21, 'adventurous': 22, 'advertised': 23, 'advice': 24, 'af': 25, 'afternoon': 26, 'afterwards': 27, 'age': 28, 'ago': 29, 'ah': 30, 'ahead': 31, 'ailment': 32, 'aint': 33, 'airy': 34, 'aisle': 35, 'aka': 36, 'ale': 37, 'alert': 38, 'alike': 39, 'alive': 40, 'allday': 41, 'allowed': 42, 'allowing': 43, 'allows': 44, 'alltime': 45, 'almost': 46, 'alone': 47, 'along': 48, 'alotta': 49, 'already': 50, 'also': 51, 'although': 52, 'always': 53, 'amazing': 54, 'amber': 55, 'amongst': 56, 'amount': 57, 'amplify': 58, 'anger': 59, 'angry': 60, 'animal': 61, 'ankle': 62, 'another': 63, 'anti': 64, 'antianxiety': 65, 'anticipating': 66, 'anxiety': 67, 'anxious': 68, 'anymore': 69, 'anyone': 70

In [346]:
corpus = [dictionary.doc2bow(text) for text in texts]
corpus

[[(0, 1),
  (1, 12),
  (2, 2),
  (3, 6),
  (4, 1),
  (5, 1),
  (6, 1),
  (7, 1),
  (8, 4),
  (9, 1),
  (10, 1),
  (11, 2),
  (12, 1),
  (13, 4),
  (14, 5),
  (15, 2),
  (16, 14),
  (17, 1),
  (18, 2),
  (19, 1),
  (20, 1),
  (21, 1),
  (22, 1),
  (23, 1),
  (24, 1),
  (25, 1),
  (26, 3),
  (27, 1),
  (28, 1),
  (29, 3),
  (30, 1),
  (31, 1),
  (32, 2),
  (33, 2),
  (34, 1),
  (35, 1),
  (36, 1),
  (37, 1),
  (38, 5),
  (39, 1),
  (40, 1),
  (41, 1),
  (42, 1),
  (43, 2),
  (44, 4),
  (45, 1),
  (46, 17),
  (47, 2),
  (48, 1),
  (49, 1),
  (50, 5),
  (51, 21),
  (52, 2),
  (53, 22),
  (54, 26),
  (55, 1),
  (56, 1),
  (57, 4),
  (58, 1),
  (59, 1),
  (60, 2),
  (61, 1),
  (62, 2),
  (63, 2),
  (64, 2),
  (65, 1),
  (66, 1),
  (67, 50),
  (68, 3),
  (69, 1),
  (70, 4),
  (71, 6),
  (72, 4),
  (73, 2),
  (74, 1),
  (75, 1),
  (76, 1),
  (77, 1),
  (78, 3),
  (79, 5),
  (80, 1),
  (81, 1),
  (82, 1),
  (83, 3),
  (84, 1),
  (85, 2),
  (86, 1),
  (87, 9),
  (88, 10),
  (89, 2),
  (90, 1),
 

In [308]:
len(corpus)

47

In [309]:
tfidf = models.TfidfModel(corpus)

2019-04-10 16:05:22,801 : INFO : collecting document frequencies
2019-04-10 16:05:22,803 : INFO : PROGRESS: processing document #0
2019-04-10 16:05:22,847 : INFO : calculating IDF weights for 47 documents and 5821 features (51544 matrix non-zeros)


In [268]:
tfidf

In [310]:
corpus_tfidf = tfidf[corpus]

In [311]:
for doc in corpus_tfidf:
    print(doc)

[(0, 0.012541471560123455), (1, 0.008223751826152972), (2, 0.0054707820432803355), (3, 0.0032516676965347337), (4, 0.016764720574627922), (5, 0.01160225298588104), (6, 0.009429082340837325), (7, 0.015011913864816148), (8, 0.019634246666735525), (9, 0.019235162879320613), (10, 0.012541471560123455), (11, 0.00631150991374421), (12, 0.007830533500952527), (13, 0.008618717601889458), (14, 0.018036422432240292), (15, 0.02157732970062336), (16, 0.007587224625247712), (17, 0.013652331355341794), (18, 0.00769250163371701), (19, 0.012541471560123455), (20, 0.005518356208988048), (21, 0.016764720574627922), (22, 0.015011913864816148), (23, 0.01078866485031168), (24, 0.013652331355341794), (25, 0.005518356208988048), (26, 0.012284920593343563), (27, 0.010071029255430766), (28, 0.01078866485031168), (29, 0.007606821624966131), (30, 0.01078866485031168), (31, 0.012541471560123455), (32, 0.02014205851086153), (33, 0.02508294312024691), (34, 0.01078866485031168), (35, 0.019235162879320613), (36, 0.01

In [312]:
model = models.LsiModel(corpus_tfidf, id2word=dictionary, num_topics=300)

2019-04-10 16:05:46,662 : INFO : using serial LSI version on this node
2019-04-10 16:05:46,667 : INFO : updating model with new documents
2019-04-10 16:05:46,978 : INFO : preparing a new chunk of documents
2019-04-10 16:05:46,993 : INFO : using 100 extra samples and 2 power iterations
2019-04-10 16:05:46,994 : INFO : 1st phase: constructing (5822, 400) action matrix
2019-04-10 16:05:47,037 : INFO : orthonormalizing (5822, 400) action matrix
2019-04-10 16:05:47,805 : INFO : 2nd phase: running dense svd on (400, 47) matrix
2019-04-10 16:05:47,818 : INFO : computing the final decomposition
2019-04-10 16:05:47,819 : INFO : keeping 47 factors (discarding 0.000% of energy spectrum)
2019-04-10 16:05:47,834 : INFO : processed documents up to #47
2019-04-10 16:05:47,838 : INFO : topic #0(1.934): 0.160*"lemon" + 0.123*"cheese" + 0.120*"haze" + 0.118*"diesel" + 0.104*"blue" + 0.101*"kush" + 0.100*"blueberry" + 0.099*"og" + 0.097*"gsc" + 0.096*"sour"
2019-04-10 16:05:47,843 : INFO : topic #1(1.270

In [272]:
model

In [349]:
doc = "hike outside friends"
vec_bow = dictionary.doc2bow(doc.lower().split())
vec_lsi = model[vec_bow]  # convert the query to LSI space
print(vec_lsi)

[(0, 0.025051422394329562), (1, -0.005106730992504457), (2, 0.00877325334187307), (3, 0.013297364142104496), (4, -0.011535471675381928), (5, 0.00986296221160269), (6, 0.0040927436574304645), (7, -0.010808153511945192), (8, -0.005011008406409125), (9, 0.00434849274131924), (10, 0.003459637024457384), (11, 0.003793560788972867), (12, -0.0010992309156516531), (13, 0.0006780023156795672), (14, -0.0011693814783700141), (15, -0.006235508320651244), (16, 0.006434401526957396), (17, 0.005978623618225483), (18, 0.005318841344319512), (19, -0.002863849829002176), (20, 0.019263042628590785), (21, 0.0022142915796998577), (22, -0.00014508888018794968), (23, -0.005428548070496414), (24, 0.006533415756248214), (25, 0.008386551850245207), (26, -0.0036108368052527222), (27, 0.010073454763308577), (28, -0.009554932765957591), (29, -0.003454424594956868), (30, -0.005593227093071486), (31, 0.006346340447722787), (32, -0.014736283515689293), (33, -0.009392703116177094), (34, -0.01697966564659015), (35, 0.0

In [347]:
index = MatrixSimilarity(model[corpus]) 
index

2019-04-10 19:50:12,459 : WARNING : scanning corpus to determine the number of features (consider setting `num_features` explicitly)
2019-04-10 19:50:12,491 : INFO : creating matrix with 47 documents and 47 features


In [350]:
sims = index[vec_lsi]

In [351]:
print(list(enumerate(sims)))

[(0, 0.36851335), (1, 0.21472672), (2, 0.41094756), (3, 0.5404586), (4, 0.32674786), (5, 0.22111514), (6, 0.20592315), (7, 0.14071624), (8, 0.2928471), (9, 0.32770208), (10, 0.32938814), (11, 0.4600761), (12, 0.4713566), (13, 0.27503866), (14, 0.25820053), (15, 0.102521785), (16, 0.113534436), (17, 0.47223395), (18, 0.26747155), (19, 0.12654907), (20, 0.09342837), (21, 0.12380146), (22, 0.1675305), (23, 0.07988204), (24, 0.18212527), (25, 0.1559029), (26, 0.13714688), (27, 0.09298219), (28, 0.11437757), (29, 0.047113292), (30, 0.34360033), (31, 0.18524948), (32, 0.2958714), (33, 0.34580037), (34, 0.28221285), (35, 0.14363517), (36, 0.21242416), (37, 0.08264079), (38, 0.13103078), (39, 0.1248235), (40, 0.22795777), (41, 0.06064553), (42, 0.102642566), (43, 0.12630895), (44, 0.12535988), (45, 0.14097756), (46, 0.12490048)]


In [352]:
sims = sorted(enumerate(sims), key=lambda item: -item[1])

In [353]:
sims[:5]

[(3, 0.5404586),
 (17, 0.47223395),
 (12, 0.4713566),
 (11, 0.4600761),
 (2, 0.41094756)]